# File Structure at Three Processing Levels for the Ocean Color Instrument (OCI)

**Authors:** Anna Windle (NASA, SSAI), Ian Carroll (NASA, UMBC), Carina Poulin (NASA, SSAI)

<div class="alert alert-success" role="alert">

The following notebooks are **prerequisites** for this tutorial.

- Learn with OCI: [Data Access][oci-data-access]

</div>

<div class="alert alert-info" role="alert">

An [Earthdata Login][edl] account is required to access data from the NASA Earthdata system, including NASA ocean color data.

</div>

[edl]: https://urs.earthdata.nasa.gov/
[oci-data-access]: https://oceancolor.gsfc.nasa.gov/resources/docs/tutorials/notebooks/oci_data_access/

## Summary

In this example we will use the `earthaccess` package to access OCI Level-1B (L1B), Level-2 (L2), and Level-3 (L3) NetCDF files and open them using `xarray`.

**NetCDF** ([Network Common Data Format][netcdf]) is a binary file format for storing multidimensional scientific data (variables). It is optimized for array-oriented data access and support a machine-independent format for representing scientific data. Files ending in `.nc` are NetCDF files.

**XArray** is a [package][xarray] that supports the use of multi-dimensional arrays in Python. It is widely used to handle Earth observation data, which often involves multiple dimensions — for instance, longitude, latitude, time, and channels/bands.

[netcdf]: https://www.unidata.ucar.edu/software/netcdf/
[xarray]: https://docs.xarray.dev/

## Learning Objectives

At the end of this notebok you will know:
* How to find groups in a NetCDF file
* How to use `xarray` to open OCI data
* What key variables are present in the groups within OCI L1B, L2, and L3 files

## Contents

1. [Setup](#setup)
1. [Explore L1B File Structure](#l1b)
1. [Explore L2 File Structure](#l2)
1. [Explore L3 File Structure](#l3)

<a name="setup"></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
%pip install earthaccess
%pip install cartopy
%pip install xarray
%pip install pandas
%pip install pathlib
%pip install h5netcdf
%pip install netCDF4

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 64.9/64.9 kB 2.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 199.1/199.1 kB 8.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.9/78.9 kB 6.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 70.8 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2025.3.2
    Uninstalling fsspec-2025.3.2:
      Successfully uninstalled fsspec-2025.3.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
gcsfs 2025.3.2 requires fsspec==2025.3.2, but you have fsspec 2025.5.1 which is incompatible.
torch 2.6.0+cu124 requires nvidia-cublas-cu12==12.4.5.8; platform_system == "Linux" and platform_machine == "x86_64", but you have nvidia-cublas-cu12 12.5.3.2 which is incompatible.
torch 2.6.0+cu124 requires nvidia-cuda-cupti-cu12==12.4.127; platform_sys

## 1. Setup

Begin by importing all of the packages used in this notebook. If your kernel uses an environment defined following the guidance on the [tutorials] page, then the imports will be successful.

[tutorials]: https://oceancolor.gsfc.nasa.gov/resources/docs/tutorials

In [ ]:
import cartopy.crs as ccrs
import earthaccess
import h5netcdf
import matplotlib.pyplot as plt
import numpy as np
import xarray as xr
import pandas as pd
import pathlib

Set (and persist to your user profile on the host, if needed) your Earthdata Login credentials.

In [ ]:
auth = earthaccess.login(persist=True)

Enter your Earthdata Login username: muthumayan
Enter your Earthdata password: ··········


In [ ]:
if not auth.authenticated:
    # Ask for credentials and persist them in a .netrc file.
    auth.login(strategy="interactive", persist=True)

print(earthaccess.__version__)

0.14.0


In [ ]:
import earthaccess

# Authenticate (will prompt for login if needed)
earthaccess.login()

# Search for MODIS datasets related to "ocean color"
datasets = earthaccess.search_datasets(
    keyword="MODIS ocean color",
    platform="Aqua",  # or "Terra"
    instrument="MODIS"
)

# Print dataset titles and shortnames
for ds in datasets:
    print(f"{ds['umm']['ShortName']}")


MODISA_L2_OC
MODISA_L4b_AVW
MODISA_L4b_CARBON
MODISA_L4b_GSM
MODISA_L4m_AVW
MODISA_L4m_CARBON
MODISA_L4m_GSM
MODISA_L3b_CHL
MODISA_L3b_CHL_NRT
MODISA_L3b_FLH
MODISA_L3b_FLH_NRT
MODISA_L3b_IOP
MODISA_L3b_IOP_NRT
MODISA_L3b_KD
MODISA_L3b_KD_NRT
MODISA_L3b_NSST
MODISA_L3b_NSST_NRT
MODISA_L3b_PAR
MODISA_L3b_PAR_NRT
MODISA_L3b_PIC
MODISA_L3b_PIC_NRT
MODISA_L3b_POC
MODISA_L3b_POC_NRT
MODISA_L3b_RRS
MODISA_L3b_RRS_NRT
MODISA_L3b_SST
MODISA_L3b_SST4
MODISA_L3b_SST4_NRT
MODISA_L3b_SST_NRT
MODISA_L3m_CHL
MODISA_L3m_CHL_NRT
MODISA_L3m_FLH
MODISA_L3m_FLH_NRT
MODISA_L3m_IOP
MODISA_L3m_IOP_NRT
MODISA_L3m_KD
MODISA_L3m_KD_NRT
MODISA_L3m_NSST
MODISA_L3m_NSST_NRT
MODISA_L3m_PAR
MODISA_L3m_PAR_NRT
MODISA_L3m_PIC
MODISA_L3m_PIC_NRT
MODISA_L3m_POC
MODISA_L3m_POC_NRT
MODISA_L3m_RRS
MODISA_L3m_RRS_NRT
MODISA_L3m_SST
MODISA_L3m_SST4
MODISA_L3m_SST4_NRT
MODISA_L3m_SST_NRT
MODISA_L2_IOP
MODISA_L2_IOP_NRT
MODISA_L2_OC_NRT
MODISA_L2_SST
MODISA_L2_SST4
MODISA_L2_SST4_NRT
MODISA_L2_SST_NRT
MODISA_L1
MODISA_L1_GEO


[back to top](#contents) <a name="l1b"></a>

Now you can project the data onto a grid. If you wanna get fancy, add a coastline.

## 4. Explore L3 File Structure

At Level-3 there are binned (B) and mapped (M) products available for OCI. The L3M remote sensing reflectance (Rrs) files contain global maps of Rrs. We'll use the same `earthaccess` method to find the data.

In [ ]:
def get_ea_search_data_timespan(tspan):
  bbox = bbox = (-85, 40, -80, 43)

  results = earthaccess.search_data(
      short_name="MODISA_L3m_RRS",
      granule_name="*.MO.*.4km.*",
      temporal=tspan,
      bounding_box=bbox,
  )
  return results

In [ ]:
def print_files_in_timespan(tspan):
  start_time, end_time = tspan
  print(f'Number of files for timespan {start_time} to {end_time}: {len(results)}')
  for k,v in enumerate(results):
    print(results[k].data_links())


In [ ]:
def download_files(results):
  import pathlib
  directory = pathlib.Path("/content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/")
  directory.mkdir(exist_ok=True)
  paths = earthaccess.download(results, directory)
  print(f'Downloaded {len(paths)} files')
  return paths

### Simple EDA
Show groups within each file. Open the file using xarray and inspect the dataset contents

In [ ]:
with h5netcdf.File(paths[0]) as file:
    groups = list(file)
groups

['processing_control', 'Rrs_412', 'lat', 'lon', 'palette']

In [ ]:
dataset = xr.open_dataset(paths[0], engine='h5netcdf')
dataset

<xarray.Dataset> Size: 149MB
Dimensions:  (lat: 4320, lon: 8640, rgb: 3, eightbitcolor: 256)
Coordinates:
  * lat      (lat) float32 17kB 89.98 89.94 89.9 89.85 ... -89.9 -89.94 -89.98
  * lon      (lon) float32 35kB -180.0 -179.9 -179.9 ... 179.9 179.9 180.0
Dimensions without coordinates: rgb, eightbitcolor
Data variables:
    Rrs_412  (lat, lon) float32 149MB ...
    palette  (rgb, eightbitcolor) uint8 768B ...
Attributes: (12/64)
    product_name:                      AQUA_MODIS.20240701_20240731.L3m.MO.RR...
    instrument:                        MODIS
    title:                             MODISA Level-3 Standard Mapped Image
    project:                           Ocean Biology Processing Group (NASA/G...
    platform:                          Aqua
    source:                            satellite observations from MODIS-Aqua
    ...                                ...
    identifier_product_doi:            10.5067/AQUA/MODIS/L3M/RRS/2022
    keywords:                          Earth Science > Oceans > Ocean Optics ...
    keywords_vocabulary:               NASA Global Change Master Directory (G...
    data_bins:                         15083554
    data_minimum:                      -0.0046839975
    data_maximum:                      0.06778

In [ ]:
def prepare_file_list(paths):
  file_list = []
  for p in paths:
    wave = p.split('.')[-3]
    span = p.split('.')[-7]
    start_date = span.split('_')[0]
    end_date = span.split('_')[1]
    assert(start_date[0:4] == end_date[0:4])
    assert(start_date[4:6] == end_date[4:6])
    year = start_date[0:4]
    month = start_date[4:6]
    print(f'{year} {month} {wave} {p}')
    if not 'Rrs_' in wave:
      continue
    file_list.append((p, year, month, wave))

  sorted_list = sorted(file_list, key=lambda x: (x[1], x[2], x[3]))
  return sorted_list

In [ ]:
def process_file_list(filtered_files):
  # We select only pixels in and around Lake Erie
  min_lat = 43.0
  max_lat = 41.0
  min_lon = -84.0
  max_lon = -78.0

  curr_year = None
  curr_month = None
  mon_year_df = None

  for file in filtered_files:
    name, year, month, wavelength = file

    if year != curr_year or month != curr_month:
      # New month, year combination. Start new dataframe
      if mon_year_df is not None:
        df_clean = mon_year_df.dropna(how='all', subset=['Rrs_443','Rrs_469','Rrs_488','Rrs_531','Rrs_547','Rrs_555','Rrs_645','Rrs_667','Rrs_678'])
        print(f'Processed dataframe shape: {df_clean.shape}')
        df_clean.to_csv(f'/content/drive/MyDrive/MIDS-210/MODIS_DATAFRAMES/master_df_{curr_year}_{curr_month}.csv')
        del mon_year_df
        del df_clean
      print(f'Processing {year} {month}')
      curr_year = year
      curr_month = month
      mon_year_df = pd.DataFrame()

    dataset = xr.open_dataset(name, engine='h5netcdf')
    subset = dataset[wavelength].sel(
      lat=slice(min_lat, max_lat),      # Latitude range (south to north)
      lon=slice(min_lon, max_lon)       # Longitude range (west to east)
    )
    print(f'{year} {month} {wavelength} {subset.shape}')
    temp_df = subset.to_dataframe(name=wavelength).reset_index()
    temp_df['year'] = year
    temp_df['month'] = month
    if mon_year_df.empty:
      mon_year_df = temp_df
    else:
      mon_year_df = pd.merge(mon_year_df, temp_df, on=['lat', 'lon', 'year', 'month'], how='outer')

  if mon_year_df is not None:
    df_clean = mon_year_df.dropna(how='all', subset=['Rrs_443','Rrs_469','Rrs_488','Rrs_531','Rrs_547','Rrs_555','Rrs_645','Rrs_667','Rrs_678'])
    print(f'Processed dataframe shape: {df_clean.shape}')
    df_clean.to_csv(f'/content/drive/MyDrive/MIDS-210/MODIS_DATAFRAMES/master_df_{curr_year}_{curr_month}.csv')
    del mon_year_df
    del df_clean

In [ ]:
def remove_files(paths):
  for p in paths:
    pathlib.Path(p).unlink()

In [ ]:
for i in range(11):
  year = 2014+i
  for month in range(1,13):
    start_time = f'{year}-{month:02d}-01'
    if month == 2:
      end_time = f'{year}-{month:02d}-28'
    else:
      end_time = f'{year}-{month:02d}-30'
    print(f'{start_time} ==> {end_time}')
    tspan = (start_time, end_time)
    results = get_ea_search_data_timespan(tspan)
    print_files_in_timespan(tspan)
    paths = download_files(results)
    file_list = prepare_file_list(paths)
    process_file_list(file_list)
    remove_files(paths)



2014-01-01 ==> 2014-01-30
Number of files for timespan 2014-01-01 to 2014-01-30: 12
['https://obdaac-tea.earthdatacloud.nasa.gov/ob-cumulus-prod-public/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_412.4km.nc']
['https://obdaac-tea.earthdatacloud.nasa.gov/ob-cumulus-prod-public/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_443.4km.nc']
['https://obdaac-tea.earthdatacloud.nasa.gov/ob-cumulus-prod-public/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_488.4km.nc']
['https://obdaac-tea.earthdatacloud.nasa.gov/ob-cumulus-prod-public/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_531.4km.nc']
['https://obdaac-tea.earthdatacloud.nasa.gov/ob-cumulus-prod-public/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_469.4km.nc']
['https://obdaac-tea.earthdatacloud.nasa.gov/ob-cumulus-prod-public/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_547.4km.nc']
['https://obdaac-tea.earthdatacloud.nasa.gov/ob-cumulus-prod-public/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_555.4km.nc']
['https://obdaac-tea.earthdatacloud.nasa.

QUEUEING TASKS | :   0%|          | 0/12 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/12 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/12 [00:00<?, ?it/s]

Downloaded 12 files
2014 01 Rrs_412 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_412.4km.nc
2014 01 Rrs_443 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_443.4km.nc
2014 01 Rrs_488 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_488.4km.nc
2014 01 Rrs_531 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_531.4km.nc
2014 01 Rrs_469 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_469.4km.nc
2014 01 Rrs_547 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_547.4km.nc
2014 01 Rrs_555 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_555.4km.nc
2014 01 Rrs_667 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20140101_20140131.L3m.MO.RRS.Rrs_667.4km.nc
2014 01 Rrs_645 /content/drive/MyDrive/MIDS-

...

Downloaded 12 files
2024 11 Rrs_555 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241101_20241130.L3m.MO.RRS.Rrs_555.4km.nc
2024 11 Rrs_469 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241101_20241130.L3m.MO.RRS.Rrs_469.4km.nc
2024 11 Rrs_531 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241101_20241130.L3m.MO.RRS.Rrs_531.4km.nc
2024 11 Rrs_443 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241101_20241130.L3m.MO.RRS.Rrs_443.4km.nc
2024 11 Rrs_547 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241101_20241130.L3m.MO.RRS.Rrs_547.4km.nc
2024 11 Rrs_667 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241101_20241130.L3m.MO.RRS.Rrs_667.4km.nc
2024 11 aot_869 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241101_20241130.L3m.MO.RRS.aot_869.4km.nc
2024 11 Rrs_645 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241101_20241130.L3m.MO.RRS.Rrs_645.4km.nc
2024 11 angstrom /content/drive/MyDrive/MIDS

QUEUEING TASKS | :   0%|          | 0/12 [00:00<?, ?it/s]

PROCESSING TASKS | :   0%|          | 0/12 [00:00<?, ?it/s]

COLLECTING RESULTS | :   0%|          | 0/12 [00:00<?, ?it/s]

Downloaded 12 files
2024 12 Rrs_469 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241201_20241231.L3m.MO.RRS.Rrs_469.4km.nc
2024 12 Rrs_531 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241201_20241231.L3m.MO.RRS.Rrs_531.4km.nc
2024 12 Rrs_547 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241201_20241231.L3m.MO.RRS.Rrs_547.4km.nc
2024 12 Rrs_555 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241201_20241231.L3m.MO.RRS.Rrs_555.4km.nc
2024 12 Rrs_645 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241201_20241231.L3m.MO.RRS.Rrs_645.4km.nc
2024 12 Rrs_667 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241201_20241231.L3m.MO.RRS.Rrs_667.4km.nc
2024 12 Rrs_678 /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241201_20241231.L3m.MO.RRS.Rrs_678.4km.nc
2024 12 angstrom /content/drive/MyDrive/MIDS-210/MODIS_L3m_RRS/AQUA_MODIS.20241201_20241231.L3m.MO.RRS.angstrom.4km.nc
2024 12 aot_869 /content/drive/MyDrive/MID